In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# Import necessary libaries & datasets

In [25]:
import pandas as pd
import re
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.express as px


Load data

In [26]:
# Load the datasets
car_golf_dataset = pd.read_csv('/content/drive/MyDrive/data/car-golf-dataset.csv', delimiter=';')
car_golf_info = pd.read_csv('/content/drive/MyDrive/data/car-golf-info.csv', delimiter=';')

Size of the dataset

In [27]:
print("size of car_golf_dataset-->",car_golf_dataset.shape)
print("size of car_golf_info   -->",car_golf_info.shape)

size of car_golf_dataset--> (77744, 16)
size of car_golf_info   --> (420, 22)


# 1. Data preparation

## 1.1 Engine type

Get the columns name from car_golf_dataset

In [64]:
car_golf_dataset.columns

Index(['source_id', 'title', 'category', 'make', 'model', 'power', 'color',
       'capacity', 'transmission', 'fuel', 'construction_year', 'price_net',
       'price_gross', 'added', 'mileage', 'url', 'multiple_engine_types'],
      dtype='object')

To get better understanding of engine type investigasting the car_golf_info

In [65]:
car_golf_info[['modification', 'parsed_engine_type']].head(-20)

modification parsed_engine_type
0                                  Golf 2.0 TDI                TDI
1                 Golf 1.6 TDI DPF Trendline M5                TDI
2                 Golf 1.6 TDI DPF Trendline M5                TDI
3                Golf 1.6 TDI DPF BlueMotion M5                TDI
4               Golf 1.6 TDI DPF Comfortline M5                TDI
..                                          ...                ...
395       Golf Variant 1.5 eTSI OPF R-Line Aut.               eTSI
396         Golf Variant 1.5 eTSI OPF Life Aut.               eTSI
397     Golf Variant 2.0 TSI Style 4Motion Aut.                TSI
398  Golf Variant 2.0 TSI Alltrack 4Motion Aut.                TSI
399                 Golf 2.0 TSI R 4Motion Aut.                TSI

[400 rows x 2 columns]

Print the unique engine type from the car_golf_info

In [66]:
# Get the count of unique engine types
engine_type_counts = car_golf_info[ 'parsed_engine_type'].value_counts()

# Display the counts
print(engine_type_counts)

parsed_engine_type
TSI                       228
TDI                       127
eTSI                       23
TDI-CR                      9
GTI                         7
R                           3
TSI eHybrid                 3
GTD                         2
e-Golf                      2
TSI Plug-In-Hybrid GTE      1
TSI GTE                     1
Name: count, dtype: int64


### **extract_engine_type** function

This function extract the engine type from the **title** of car_golf_dataset

In [67]:
# Function to extract engine type
def extract_engine_type(title):
    title = title.lower()  # Convert title to lowercase for case-insensitivity

    # Enhanced regex for capturing engine types, including "e" variations like eTSI and eHybrid
    patterns = r'\b((?:\d+(?:\.\d+)?\s*)?(tsi|etsi|tdi|gti|gtd|hybrid|ehybrid))\b'

    # Find all matches
    matches = re.findall(patterns, title)

    if matches:
        engine_type = matches[0][1].lower()  # Extract first detected engine type

        # Handling "e" variations like "eTSI" or "eHybrid" to match common types
        if engine_type.startswith('e'):
            engine_type = engine_type[1:]  # Remove the "e" prefix to normalize

        return engine_type
    else:
        return 'unknown'  # Return 'unknown' if no matches found

# Apply the function to create the engine_type column
car_golf_dataset['engine_type'] = car_golf_dataset['title'].apply(extract_engine_type)

# Get counts for each engine type
engine_type_counts = car_golf_dataset['engine_type'].value_counts()

# Debugging: Show problematic rows with 'unknown' engine types for inspection
unknown_engine_types = car_golf_dataset[car_golf_dataset['engine_type'] == 'unknown']

# Display updated data for cases where 'Golf' is in the title
golf_rows = car_golf_dataset.loc[car_golf_dataset['title'].str.contains('Golf', case=False), ['title', 'engine_type']].head(20)

engine_type_counts


engine_type
tsi        31364
tdi        19130
unknown    17435
gti         6658
gtd         2167
hybrid       990
Name: count, dtype: int64

In [68]:
unknown_engine_types[['title', 'engine_type']]

title engine_type
0      Volkswagen Golf -Black Weeks-Fahrzeug, täglich...     unknown
13     Volkswagen Golf VII DSG HIGHLINE SPORT LED*NAV...     unknown
20     Volkswagen Golf Bluetooth Navi Klima Einparkhilfe     unknown
23     Volkswagen Golf VII Sportsvan DSG KLIMA Navi p...     unknown
24     Volkswagen Golf VII Sportsvan Comfort SHZ,AHK,...     unknown
...                                                  ...         ...
77708  Volkswagen Golf VII Lim. Trendline Automatik  ...     unknown
77712         Volkswagen Golf Sportsvan VII NAVI ACC AHK     unknown
77723  Volkswagen GOLF VII VARIANT COMFORTLINE 150PS ...     unknown
77731  Volkswagen Golf VII Variant Highline Navi AHK ...     unknown
77738  Volkswagen Golf VIII Active LED Navi ACC  Fern...     unknown

[17435 rows x 2 columns]

In [69]:
# Filter the dataset for rows where engine_type is 'unknown'
unknown_engine_types = car_golf_dataset[car_golf_dataset['engine_type'] == 'unknown'][['title', 'engine_type']]

unknown_engine_types

title engine_type
0      Volkswagen Golf -Black Weeks-Fahrzeug, täglich...     unknown
13     Volkswagen Golf VII DSG HIGHLINE SPORT LED*NAV...     unknown
20     Volkswagen Golf Bluetooth Navi Klima Einparkhilfe     unknown
23     Volkswagen Golf VII Sportsvan DSG KLIMA Navi p...     unknown
24     Volkswagen Golf VII Sportsvan Comfort SHZ,AHK,...     unknown
...                                                  ...         ...
77708  Volkswagen Golf VII Lim. Trendline Automatik  ...     unknown
77712         Volkswagen Golf Sportsvan VII NAVI ACC AHK     unknown
77723  Volkswagen GOLF VII VARIANT COMFORTLINE 150PS ...     unknown
77731  Volkswagen Golf VII Variant Highline Navi AHK ...     unknown
77738  Volkswagen Golf VIII Active LED Navi ACC  Fern...     unknown

[17435 rows x 2 columns]

In [70]:
# Grouping unique parsed_engine_type with their associated modification
engine_type_modifications = car_golf_info.groupby('parsed_engine_type')['modification'].unique()

# Display the result
for engine_type, modifications in engine_type_modifications.items():
    print(f"Engine Type: {engine_type}")
    print(f"Modifications: {modifications}")
    print("-" * 40)


Engine Type: GTD
Modifications: ['Golf 2.0 GTD DSG' 'Golf 2.0 GTD M6']
----------------------------------------
Engine Type: GTI
Modifications: ['Golf 2.0 GTI DSG A6' 'Golf 2.0 GTI M6' 'Golf 2.0 GTI' 'Golf GTI DSG'
 'Golf GTI M6']
----------------------------------------
Engine Type: R
Modifications: ['Golf 2.0 R M6' 'Golf 2.0 R DSG A6' 'Golf Variant 2.0 R 4Motion']
----------------------------------------
Engine Type: TDI
Modifications: ['Golf 2.0 TDI' 'Golf 1.6 TDI DPF Trendline M5'
 'Golf 1.6 TDI DPF BlueMotion M5' 'Golf 1.6 TDI DPF Comfortline M5'
 'Golf 1.6 TDI DPF DSG Trendline A7' 'Golf 1.6 TDI DPF DSG Comfortline A7'
 'Golf 1.6 TDI DPF' 'Golf 2.0 TDI DPF DSG Highline A6'
 'Golf 2.0 TDI DPF Trendline M5' 'Golf 2.0 TDI DPF Comfortline M5'
 'Golf 2.0 TDI DPF DSG Trendline A6' 'Golf 2.0 TDI DPF Highline M5'
 'Golf 2.0 TDI DPF DSG Comfortline A6'
 'Golf 2.0 TDI DPF 4Motion Highline M6' 'Golf 2.0 TDI DPF'
 'Golf 2.0 TDI DPF 4Motion Comfortline M6' 'Golf 2.0 TDI DPF Highline M6'
 'Gol

In [71]:
car_golf_info['submodel'].unique()

array(['VW GOLF (2008 - 2012)  VI Cabrio',
       'VW GOLF (2008 - 2012)  VI Hečbekas',
       'VW GOLF (2008 - 2012)  VI Universalas',
       'VW GOLF PLUS (2008 - 2013) VI  Vienatūris',
       'VW GOLF (2012 - 2020) VII Hečbekas',
       'VW GOLF (2012 - 2020) VII Universalas',
       'VW GOLF ALLTRACK (2014 - 2020)  Universalas',
       'VW GOLF SPORTSVAN (2014 - 2020)  Universalas',
       'VW GOLF (2019 - ) VIII Hečbekas',
       'VW GOLF (2019 - ) VIII Universalas'], dtype=object)

In [72]:
car_golf_dataset[['title', 'engine_type', 'category']].head(20)

title engine_type  \
0   Volkswagen Golf -Black Weeks-Fahrzeug, täglich...     unknown   
1   Volkswagen Golf Var. VII 2.0 TDI DSG GTD Sport...         tdi   
2   Volkswagen Golf VII Sportsvan Van/Lounge 2.0 T...         tdi   
3   Volkswagen Golf  Sportsvan 1.2 TSI Lounge AAC ...         tsi   
4   Volkswagen Golf 7 Sportsvan Allstar 1.6 TDI BM...         tdi   
5   Volkswagen Golf VII Sportsvan Comfortline 1.6T...         tdi   
6   Volkswagen Golf VII Variant 2.0 TDI DSG+Highli...         tdi   
7   Volkswagen Golf VII Variant 2.0 TDI Lounge -Eu...         tdi   
8   Volkswagen Golf VII Variant 2.0 TDI Lounge -Eu...         tdi   
9   Volkswagen Golf VII Sportsvan 1.2 TSI  Klimaau...         tsi   
10  Volkswagen Golf VII Variant 2.0 TDI ALLSTAR R-...         tdi   
11  Volkswagen Golf VII Sportsvan 1.4 TSI (BlueMot...         tsi   
12     Volkswagen Golf VII 1.2 TSI BMT Lounge SITZHZG         tsi   
13  Volkswagen Golf VII DSG HIGHLINE SPORT LED*NAV...     unknown   
14  Volkswagen Golf Var. VII R 2.0 TSI DSG 4Mo. AC...         tsi   
15      Volkswagen Golf GTD BlueMotion Technology DSG         gtd   
16  Volkswagen Golf VII Sportsvan 1.6 TDI GRA*NAVI...         tdi   
17  Volkswagen Golf 2.0 TDI Variant Highline BMT, ...         tdi   
18  Volkswagen Golf VII Sportsvan 1.6 TDI GRA*NAVI...         tdi   
19     Volkswagen Golf 1.6 TDI DSG BMT LOUNGE Variant         tdi   

         category  
0      Estate Car  
1      Estate Car  
2          Saloon  
3   Van / Minibus  
4          Saloon  
5   Van / Minibus  
6      Estate Car  
7      Estate Car  
8      Estate Car  
9   Van / Minibus  
10     Estate Car  
11  Van / Minibus  
12     Estate Car  
13     Estate Car  
14     Estate Car  
15         Saloon  
16  Van / Minibus  
17     Estate Car  
18         Saloon  
19     Estate Car

## 1.2 Category

Grouping unique parsed_category with their associated submodel

In [73]:
# Grouping unique parsed_category with their associated submodel
category_submodels = car_golf_info.groupby('parsed_category')['submodel'].unique()

# Display the result
for category, submodels in category_submodels.items():
    print(f"Category: {category}")
    print(f"Submodels: {submodels}")
    print("-" * 40)


Category: Cabriolet/Roadster
Submodels: ['VW GOLF (2008 - 2012)  VI Cabrio']
----------------------------------------
Category: Estate Car
Submodels: ['VW GOLF (2008 - 2012)  VI Universalas'
 'VW GOLF (2012 - 2020) VII Universalas'
 'VW GOLF ALLTRACK (2014 - 2020)  Universalas'
 'VW GOLF SPORTSVAN (2014 - 2020)  Universalas'
 'VW GOLF (2019 - ) VIII Universalas']
----------------------------------------
Category: Small Car
Submodels: ['VW GOLF (2008 - 2012)  VI Hečbekas' 'VW GOLF (2012 - 2020) VII Hečbekas'
 'VW GOLF (2019 - ) VIII Hečbekas']
----------------------------------------
Category: Van/Minibus
Submodels: ['VW GOLF PLUS (2008 - 2013) VI  Vienatūris']
----------------------------------------


Get unique categories of car_golf_dataset

In [74]:
# Get the count of unique categories
category_counts = car_golf_dataset['category'].value_counts()

# Display the counts
print(category_counts)


category
Saloon                                                  26315
Limousine                                               20237
Estate Car                                              12397
EstateCar                                                7933
Saloon, Employees Car                                    3699
Saloon, Demonstration Vehicle                             927
Van / Minibus                                             898
Estate Car, Employees Car                                 707
Saloon, Pre-Registration                                  618
Small Car                                                 582
Cabriolet / Roadster                                      550
Van                                                       516
Other                                                     426
Estate Car, Demonstration Vehicle                         381
Cabrio                                                    332
Estate Car, Pre-Registration                              302

### map_category function

This function map category based on title of car_golf_dataset

In [75]:
# Define submodel keywords and their corresponding categories
keyword_to_category = {
    'SPORTSVAN': 'Estate Car',
    'ALLTRACK': 'Estate Car',
    'Cabrio': 'Cabriolet',
    'Limousine': 'Limousine'
}

# Function to map category based on title
def map_category(row):
    title = row['title'].lower()  # Convert title to lowercase for case-insensitivity
    current_category = row['category']  # Get the current category
    for keyword, new_category in keyword_to_category.items():
        if keyword.lower() in title:  # Check if the keyword exists in the title
            return new_category  # Return the new category if a match is found
    return current_category  # Return the original category if no match found

# Create a copy of the original category column for comparison
original_categories = car_golf_dataset['category'].copy()

# Apply the mapping function to update the existing category column conditionally
car_golf_dataset['category'] = car_golf_dataset.apply(map_category, axis=1)

# Count how many categories were updated
updated_count = (car_golf_dataset['category'] != original_categories).sum()

# Identify updated rows
updated_rows = car_golf_dataset[car_golf_dataset['category'] != original_categories]

# Display results
print(f"Number of updated categories: {updated_count}")
print("\nUpdated Rows:")
updated_rows[['title', 'category']]

Number of updated categories: 3127

Updated Rows:


title    category
2      Volkswagen Golf VII Sportsvan Van/Lounge 2.0 T...  Estate Car
3      Volkswagen Golf  Sportsvan 1.2 TSI Lounge AAC ...  Estate Car
4      Volkswagen Golf 7 Sportsvan Allstar 1.6 TDI BM...  Estate Car
5      Volkswagen Golf VII Sportsvan Comfortline 1.6T...  Estate Car
9      Volkswagen Golf VII Sportsvan 1.2 TSI  Klimaau...  Estate Car
...                                                  ...         ...
77712         Volkswagen Golf Sportsvan VII NAVI ACC AHK  Estate Car
77713  Volkswagen Golf VI Cabriolet GTI|1HD|Leder|Bi-...   Cabriolet
77724              Volkswagen Golf 1.6 TDI BMT Cabriolet   Cabriolet
77729         Volkswagen Golf 2.0 TDI LIFE BMT Cabriolet   Cabriolet
77737                  Volkswagen Golf 1.4 TSI Cabriolet   Cabriolet

[3127 rows x 2 columns]

Get the count of unique categories


In [76]:
# Get the count of unique categories
category_counts = car_golf_dataset['category'].value_counts()

# Display the counts
print(category_counts)


category
Saloon                                                  25847
Limousine                                               20083
Estate Car                                              14611
EstateCar                                                7582
Saloon, Employees Car                                    3697
Saloon, Demonstration Vehicle                             925
Cabriolet                                                 873
Estate Car, Employees Car                                 701
Saloon, Pre-Registration                                  618
Small Car                                                 572
Other                                                     416
Estate Car, Demonstration Vehicle                         361
Estate Car, Pre-Registration                              299
SportsCar                                                 207
SmallCar                                                  197
Sports Car / Coupe                                        190

### categorize_entry

This function group the main category of car_gofl_dataset

In [77]:
# Function to categorize entries based on keywords
def categorize_entry(category):
    category = category.lower().replace(' ', '')  # Normalize: lowercase and remove spaces
    if 'saloon' in category:
        return 'Saloon'
    elif 'limousine' in category:
        return 'Limousine'
    elif 'estatecar' in category or 'estatecar' in category:
        return 'Estate Car'
    #elif 'van' in category or 'minibus' in category:
      #  return 'Van / Minibus'
    elif 'smallcar' in category or 'smallcar' in category:
        return 'Small Car'
    elif 'cabriolet' in category or 'roadster' in category:
        return 'Cabriolet / Roadster'
   # elif 'sportscar' in category:
      #  return 'SportsCar'
    else:
        return 'Other'

# Apply the function to create a new category column or update the existing one
car_golf_dataset['category'] = car_golf_dataset['category'].apply(categorize_entry)

# Display the updated category counts
updated_category_counts = car_golf_dataset['category'].value_counts()
print(updated_category_counts)


category
Saloon                  31105
Estate Car              23607
Limousine               20083
Other                    1278
Cabriolet / Roadster      898
Small Car                 773
Name: count, dtype: int64


In [78]:
car_golf_dataset['category'].unique()

array(['Estate Car', 'Saloon', 'Cabriolet / Roadster', 'Other',
       'Small Car', 'Limousine'], dtype=object)

In [79]:
car_golf_dataset['engine_type'].unique()

array(['unknown', 'tdi', 'tsi', 'gtd', 'gti', 'hybrid'], dtype=object)

In [80]:
car_golf_dataset[['title', 'engine_type', 'category']]

title engine_type  \
0      Volkswagen Golf -Black Weeks-Fahrzeug, täglich...     unknown   
1      Volkswagen Golf Var. VII 2.0 TDI DSG GTD Sport...         tdi   
2      Volkswagen Golf VII Sportsvan Van/Lounge 2.0 T...         tdi   
3      Volkswagen Golf  Sportsvan 1.2 TSI Lounge AAC ...         tsi   
4      Volkswagen Golf 7 Sportsvan Allstar 1.6 TDI BM...         tdi   
...                                                  ...         ...   
77739  Volkswagen Golf VIII 8 Style 1.5 eTSI Rückfahr...         tsi   
77740  Volkswagen Golf Active 1.5 TSI Standh. Navi Si...         tsi   
77741                        Volkswagen Golf 2.0 TSI GTI         tsi   
77742  Volkswagen Golf VIII Variant 2.0 TDI DSG Life ...         tdi   
77743  Volkswagen Golf VIII Variant 2.0 TDI DSG LED, ...         tdi   

         category  
0      Estate Car  
1      Estate Car  
2      Estate Car  
3      Estate Car  
4      Estate Car  
...           ...  
77739      Saloon  
77740      Saloon  
77741      Saloon  
77742  Estate Car  
77743  Estate Car  

[77744 rows x 3 columns]

# 2. Data cleaning

In [81]:
car_golf_dataset.head()

source_id                                              title    category  \
0  286354023  Volkswagen Golf -Black Weeks-Fahrzeug, täglich...  Estate Car   
1  312826845  Volkswagen Golf Var. VII 2.0 TDI DSG GTD Sport...  Estate Car   
2  311592214  Volkswagen Golf VII Sportsvan Van/Lounge 2.0 T...  Estate Car   
3  312569111  Volkswagen Golf  Sportsvan 1.2 TSI Lounge AAC ...  Estate Car   
4  299066532  Volkswagen Golf 7 Sportsvan Allstar 1.6 TDI BM...  Estate Car   

         make model  power color  capacity            transmission    fuel  \
0  volkswagen  golf    123   NaN      1395          Manual gearbox  Petrol   
1  volkswagen  golf    181   NaN      1968  Automatic transmission  Diesel   
2  volkswagen  golf    148   NaN      1968  Automatic transmission  Diesel   
3  volkswagen  golf    109   NaN      1197          Manual gearbox  Petrol   
4  volkswagen  golf    109   NaN      1598          Manual gearbox  Diesel   

            construction_year  price_net  price_gross  \
0  2015-01-01 00:00:00.000000    10466.0        12140   
1  2017-01-01 00:00:00.000000    19784.0        22950   
2  2016-01-01 00:00:00.000000        NaN        15920   
3  2015-01-01 00:00:00.000000        NaN        14900   
4  2016-01-01 00:00:00.000000        NaN        13450   

                        added  mileage  \
0  2020-11-26 01:11:25.000000    76973   
1  2020-11-26 01:12:39.000000    91800   
2  2020-11-26 01:12:55.000000    92004   
3  2020-11-26 01:29:05.000000    56150   
4  2020-11-26 01:29:40.000000    88500   

                                                 url multiple_engine_types  \
0  https://suchen.mobile.de/fahrzeuge/details.htm...                  None   
1  https://suchen.mobile.de/fahrzeuge/details.htm...              tdi, gtd   
2  https://suchen.mobile.de/fahrzeuge/details.htm...                  None   
3  https://suchen.mobile.de/fahrzeuge/details.htm...                  None   
4  https://suchen.mobile.de/fahrzeuge/details.htm...                  None   

  engine_type  
0     unknown  
1         tdi  
2         tdi  
3         tsi  
4         tdi

In [82]:
def detect_suspicious_rows(car_golf_dataset):
    # Function to detect issues in each row
    def check_issues(row):
        issues = []

        # Safe retrieval of values to avoid AttributeError
        title = str(row['title']).lower() if pd.notna(row['title']) else ""
        fuel = str(row['fuel']).lower() if pd.notna(row['fuel']) else ""
        transmission = str(row['transmission']).lower() if pd.notna(row['transmission']) else ""
        engine_type = str(row['engine_type']).lower() if pd.notna(row['engine_type']) else ""
        power = row['power']
        mileage = row['mileage']
        price_net = row['price_net']
        construction_year = row['construction_year']

        # Check for DSG in title but transmission is manual
        if 'dsg' in title and 'manual' in transmission:
            issues.append("Title mentions DSG, but transmission is manual.")

        # Check for hybrid in title but fuel is petrol
        if 'hybrid' in title and 'petrol' in fuel:
            issues.append("Title suggests hybrid, but fuel is petrol.")

        # Check for engine type mismatch (e.g., TSI in title but not in engine_type)
        if 'tsi' in title and engine_type != 'tsi':
            issues.append("Title mentions TSI, but engine_type is not TSI.")
        if 'tdi' in title and engine_type != 'tdi':
            issues.append("Title mentions TDI, but engine_type is not TDI.")

        # Detect missing power value in title
        #if re.search(r'\b\d+(hp|kw)\b', title) is None and pd.isna(power):
            #issues.append("Power value is missing from both title and power field.")

        # Detect low mileage for an older car
        try:
            year = int(str(construction_year)[:4])  # Extract the year
            if mileage < 5000 and year < 2020:
                issues.append("Unusually low mileage for an older car.")
        except ValueError:
            pass

        # Check for missing price values
        #if pd.isna(price_net) or price_net <= 0:
            #issues.append("Missing or invalid net price.")

        return "; ".join(issues)

    # Apply the checks to each row
    car_golf_dataset['suspicious_notes'] = car_golf_dataset.apply(check_issues, axis=1)

    # Filter rows with issues
    suspicious_rows = car_golf_dataset[car_golf_dataset['suspicious_notes'] != ""]
    return suspicious_rows


# Apply the cleaning function to the car_golf_dataset DataFrame
suspicious_data = detect_suspicious_rows(car_golf_dataset)
suspicious_data


source_id                                              title  \
53     308055570  Volkswagen Golf VII Sportsvan 1.0TSI IQ.DRIVE ...   
139    299375975  Volkswagen Golf Var. VII 1.5 TSI DSG 2x R-Line...   
170    317280209  Volkswagen Golf Var. VII 1.6 TDI Comfortline N...   
205    317525296  Volkswagen Golf VII Variant GTD 2.0TDI *XENON*...   
254    319383525  Volkswagen Golf VII 1.4 TSI Comfortline Navi A...   
...          ...                                                ...   
77651  406509701   Volkswagen Golf GTI Golf GTI Performance 2.0 TSI   
77661  406513850   Volkswagen Golf 7 GTD 2.0 TDI 5p. BlueMotion Tec   
77670  406510322  Volkswagen Golf VI*Cabriolet*GTI*2.0*TSI*BBS*B...   
77686  406505667   Volkswagen Golf GTD 2.0 TDI 5p. BlueMotion Techn   
77688  406505390  Volkswagen VW Golf 7 R-Line GTI PACK - 1.4 TSI...   

                   category        make model  power            color  \
53               Estate Car  volkswagen  golf    114              NaN   
139              Estate Car  volkswagen  golf    148              NaN   
170              Estate Car  volkswagen  golf    114              NaN   
205              Estate Car  volkswagen  golf    181              NaN   
254              Estate Car  volkswagen  golf    123              NaN   
...                     ...         ...   ...    ...              ...   
77651                Saloon  Volkswagen  Golf    227   Black Metallic   
77661                Saloon  Volkswagen  Golf    181            White   
77670  Cabriolet / Roadster  Volkswagen  Golf    208  Silver Metallic   
77686                Saloon  Volkswagen  Golf    181   White Metallic   
77688                Saloon  Volkswagen  Golf    121   White Metallic   

       capacity            transmission                 fuel  \
53          999          Manual gearbox               Petrol   
139        1498  Automatic transmission               Petrol   
170        1598          Manual gearbox               Diesel   
205        1968          Manual gearbox               Diesel   
254        1395          Manual gearbox               Petrol   
...         ...                     ...                  ...   
77651      1984          Semi-automatic               Petrol   
77661      1968               Automatic               Diesel   
77670      1984          Manual gearbox  Petrol, E10-enabled   
77686      1968          Manual gearbox               Diesel   
77688      1390               Automatic               Petrol   

                construction_year  price_net  price_gross  \
53     2019-01-01 00:00:00.000000    15915.0        18939   
139    2019-01-01 00:00:00.000000    26285.0        31279   
170    2019-01-01 00:00:00.000000    16765.0        19950   
205    2016-01-01 00:00:00.000000        NaN        18900   
254    2018-01-01 00:00:00.000000    15445.0        18380   
...                           ...        ...          ...   
77651  2015-10-01 03:00:00.000000        NaN        17499   
77661  2015-06-01 03:00:00.000000        NaN        18990   
77670  2013-05-01 03:00:00.000000        NaN        14999   
77686  2016-10-01 03:00:00.000000        NaN        16900   
77688  2013-02-01 02:00:00.000000        NaN        17900   

                            added  mileage  \
53     2021-01-24 00:09:37.000000     3106   
139    2021-01-24 00:57:14.000000     1571   
170    2021-02-07 03:32:30.000000     4560   
205    2021-02-11 03:33:31.000000    52400   
254    2021-03-11 03:46:33.000000      248   
...                           ...      ...   
77651  2024-10-21 09:29:35.000000   160000   
77661  2024-10-21 09:29:42.000000   140800   
77670  2024-10-21 09:30:13.000000    71000   
77686  2024-10-21 09:30:29.000000   150000   
77688  2024-10-21 09:30:30.000000   136110   

                                                     url  \
53     https://suchen.mobile.de/auto-inserat/volkswag...   
139    https://suchen.mobile.de/auto-inserat/volkswag...   
170    https://suchen.mobile.de/auto-inser

In [83]:
# Filter rows with issues
suspicious_rows = car_golf_dataset[car_golf_dataset['suspicious_notes'] != ""]

# Keep only relevant columns
relevant_columns = ['source_id', 'title', 'transmission', 'fuel',  'mileage', 'engine_type', 'suspicious_notes']
suspicious_rows[relevant_columns]


source_id                                              title  \
53     308055570  Volkswagen Golf VII Sportsvan 1.0TSI IQ.DRIVE ...   
139    299375975  Volkswagen Golf Var. VII 1.5 TSI DSG 2x R-Line...   
170    317280209  Volkswagen Golf Var. VII 1.6 TDI Comfortline N...   
205    317525296  Volkswagen Golf VII Variant GTD 2.0TDI *XENON*...   
254    319383525  Volkswagen Golf VII 1.4 TSI Comfortline Navi A...   
...          ...                                                ...   
77651  406509701   Volkswagen Golf GTI Golf GTI Performance 2.0 TSI   
77661  406513850   Volkswagen Golf 7 GTD 2.0 TDI 5p. BlueMotion Tec   
77670  406510322  Volkswagen Golf VI*Cabriolet*GTI*2.0*TSI*BBS*B...   
77686  406505667   Volkswagen Golf GTD 2.0 TDI 5p. BlueMotion Techn   
77688  406505390  Volkswagen VW Golf 7 R-Line GTI PACK - 1.4 TSI...   

                 transmission                 fuel  mileage engine_type  \
53             Manual gearbox               Petrol     3106         tsi   
139    Automatic transmission               Petrol     1571         tsi   
170            Manual gearbox               Diesel     4560         tdi   
205            Manual gearbox               Diesel    52400         gtd   
254            Manual gearbox               Petrol      248         tsi   
...                       ...                  ...      ...         ...   
77651          Semi-automatic               Petrol   160000         gti   
77661               Automatic               Diesel   140800         gtd   
77670          Manual gearbox  Petrol, E10-enabled    71000         gti   
77686          Manual gearbox               Diesel   150000         gtd   
77688               Automatic               Petrol   136110         gti   

                                      suspicious_notes  
53             Unusually low mileage for an older car.  
139            Unusually low mileage for an older car.  
170            Unusually low mileage for an older car.  
205    Title mentions TDI, but engine_type is not TDI.  
254            Unusually low mileage for an older car.  
...                                                ...  
77651  Title mentions TSI, but engine_type is not TSI.  
77661  Title mentions TDI, but engine_type is not TDI.  
77670  Title mentions TSI, but engine_type is not TSI.  
77686  Title mentions TDI, but engine_type is not TDI.  
77688  Title mentions TSI, but engine_type is not TSI.  

[6235 rows x 7 columns]

### 2.1 title and category mismatch

In [84]:
# Load dataset
#car_golf_dataset = pd.read_csv('/content/drive/MyDrive/data/car-golf-dataset.csv', delimiter=';')

# List of categories to check for in the title
categories_to_check = [
    'Saloon', 'Estate Car', 'Limousine', 'Van / Minibus',
    'Other', 'Small Car', 'Cabriolet / Roadster', 'SportsCar'
]

# Function to check if any category is present in the title
def check_category_in_title(title, categories_list):
    title = title.lower()  # Convert to lowercase for case-insensitive matching
    for category in categories_list:
        if category.lower() in title:  # Check if the category exists in the title
            return category  # Return the matching category found
    return None  # If no match, return None

# Filter rows where the category name is present in the title
filtered_data = car_golf_dataset[car_golf_dataset['title'].apply(lambda x: check_category_in_title(x, categories_to_check)).notna()]

# Display relevant columns ('title' and 'category') for inspection
filtered_data[['title', 'category']]


title   category
2439   Volkswagen Golf VIII Limousine 2.0 TSI R 4Moti...  Limousine
2631   Volkswagen Golf 7 1.6 TDI Allstar BMT Limousin...  Limousine
3252   Volkswagen Golf VII Limousine 2.0 TSI GTI DSG ...  Limousine
7040   Volkswagen Golf Limousine Automatik **Navi*LED...  Limousine
9721   Volkswagen Golf VII Limousine 1.6 TDI SCR DSG ...  Limousine
...                                                  ...        ...
73892  Volkswagen Golf 2.0 TDI Limousine Allstar*NAVI...  Limousine
74252  Volkswagen Golf VII Limousine GTI 2.0 DSG ** P...  Limousine
74465  Volkswagen Golf VII Limousine Trendline BMT/St...  Limousine
76612  Volkswagen Golf 7 VII 2.0 TSI GTI BMT Limousin...  Limousine
77674  Volkswagen Golf VII Limousine 1.6 TDI SCR DSG ...  Limousine

[67 rows x 2 columns]

Note: I have updated the category according to the title , so the category have been already updted using the map_category function

### 2.2 multiple engine types in title

In [85]:
# List of possible engine types to check for
engine_types = ['tsi', 'tdi', 'gtd', 'gti', 'hybrid', 'ehybrid']

# Function to check for multiple engine types in the title
def check_multiple_engine_types(title):
    # Convert to lowercase for case-insensitivity
    title = title.lower()

    # Find all matching engine types in the title using regular expression
    matches = [engine for engine in engine_types if re.search(r'\b' + re.escape(engine) + r'\b', title)]

    if len(matches) > 1:  # If more than one engine type found
        return ', '.join(matches)  # Return engine types
    return None  # Return None if no multiple engine types are found

# Apply the function to the DataFrame and create a new column to indicate multiple engine types
car_golf_dataset['multiple_engine_types'] = car_golf_dataset['title'].apply(check_multiple_engine_types)

# Filter rows where multiple engine types are found
multiple_engine_rows = car_golf_dataset[car_golf_dataset['multiple_engine_types'].notna()]

# Display relevant columns for inspection (titles with multiple engine types)
multiple_engine_rows[['title', 'multiple_engine_types']]



title multiple_engine_types
1      Volkswagen Golf Var. VII 2.0 TDI DSG GTD Sport...              tdi, gtd
59     Volkswagen Golf Var. VII 2.0 TDI GTD AHK PANO ...              tdi, gtd
156    Volkswagen Golf Var. VII 2.0 TDI DSG GTD NAVI-...              tdi, gtd
283    Volkswagen Golf 2.0 TSI DSG BMT GTI Performanc...              tsi, gti
327    Volkswagen VOLKSWAGEN Golf Golf GTI Perf. 2.0 ...              tsi, gti
...                                                  ...                   ...
77661   Volkswagen Golf 7 GTD 2.0 TDI 5p. BlueMotion Tec              tdi, gtd
77670  Volkswagen Golf VI*Cabriolet*GTI*2.0*TSI*BBS*B...              tsi, gti
77686   Volkswagen Golf GTD 2.0 TDI 5p. BlueMotion Techn              tdi, gtd
77688  Volkswagen VW Golf 7 R-Line GTI PACK - 1.4 TSI...              tsi, gti
77741                        Volkswagen Golf 2.0 TSI GTI              tsi, gti

[6990 rows x 2 columns]

Note: There have 6990 number of entries where have multiple engine type in the title


I have taken engine type whcih appears first in the title

### 2.3 engine_type and fuel_type mismatch

In [86]:
# Get the count of unique values in the 'fuel' column
fuel_counts = car_golf_dataset['fuel'].value_counts()

# Display the counts
print("Count of Unique Fuel Values:")
print(fuel_counts)

Count of Unique Fuel Values:
fuel
Petrol                                                    40875
Diesel                                                    26406
Petrol, E10-enabled                                        6102
Hybrid (petrol/electric)                                   1561
Hybrid (petrol/electric), Plug-in hybrid                    840
Natural Gas                                                 551
Electric                                                    298
Other                                                       257
Hybrid (petrol/electric), E10-enabled, Plug-in hybrid       133
Hybrid (petrol/electric), E10-enabled                        86
Diesel, Biodiesel Suitable                                   66
LPG                                                          49
Diesel, E10-enabled                                          14
Diesel, Suitable for Vegetable Oil                            5
Diesel, Biodiesel Suitable, Suitable for Vegetable Oil        4
Natura

Filter the rows where engine_type is 'hybrid' and fuel is 'Petrol'

In [87]:
# Filter the rows where engine_type is 'hybrid' and fuel is 'Petrol'
hybrid_petrol_data = car_golf_dataset[(car_golf_dataset['engine_type'] == 'hybrid') & (car_golf_dataset['fuel'] == 'Petrol')]

hybrid_petrol_data[['title', 'engine_type', 'fuel']]

title engine_type    fuel
2626   Volkswagen Golf VIII Lim. Style eHybrid DSG~LE...      hybrid  Petrol
3703                Volkswagen Golf VIII 1.4 eHybrid GTE      hybrid  Petrol
11323  Volkswagen Golf VIII Lim. GTE eHybrid LED NAVI...      hybrid  Petrol
13315  Volkswagen Golf VIII 1.4 eHybrid GTE DSG + AHK...      hybrid  Petrol
15410  Volkswagen Golf Style 1.4 eHybrid DSG LED-Plus...      hybrid  Petrol
16419         Volkswagen Golf 1.4 GTE Plug-In-Hybrid DSG      hybrid  Petrol
16547  Volkswagen Golf GTE VIII 1.4 eHybrid DSG NAVI,...      hybrid  Petrol
22093  Volkswagen Golf VIII 1.4 eHybrid Style Style e...      hybrid  Petrol
26710  Volkswagen Golf VIII 1.4 Style eHybrid AHK NAV...      hybrid  Petrol
45920  Volkswagen Golf GTE 1,4 l E-Hybrid Rückfahrkam...      hybrid  Petrol
51579  Volkswagen Golf 8 Style eHybrid IQ-LED/Navi/AC...      hybrid  Petrol
56111  Volkswagen Golf VIII GTE 1.4 eHybrid DSG NAVI ...      hybrid  Petrol
57876  Volkswagen Golf VIII 1.4 eHybrid GTE DSG NAVI ...      hybrid  Petrol
62109  Volkswagen Golf GTE 1,5l eHybrid 130kW/ 85kW*D...      hybrid  Petrol
62872  Volkswagen Golf VIII Style 1.5 eHybrid DSG**LE...      hybrid  Petrol
65531  Volkswagen Golf GTE  1,5 l eHybrid DSG AHK DCC...      hybrid  Petrol
66208  Volkswagen Golf GTE 1.5 l eHybrid OPF / 85 kW ...      hybrid  Petrol
66799  Volkswagen Golf GTE 1,5 l DSG eHybrid+AHK+DCC+...      hybrid  Petrol
70373  Volkswagen Golf GTE 1,5 l eHybrid DSG HUD LED ...      hybrid  Petrol
74818  Volkswagen Golf  GTE eHybrid Pan/Kam/Keyl/HUD/...      hybrid  Petrol
76903  Volkswagen Golf Style eHybrid IQ-Matrix/Kamera...      hybrid  Petrol

In [88]:
hybrid_petrol_data.shape

(21, 19)

There have 21 entries where the engine type and fuel type mismatch

In [89]:
def update_fuel_type_to_hybrid(dataset):
    """
    Update fuel type to 'Hybrid' where engine_type is 'hybrid' and fuel is 'Petrol'.

    Parameters:
        dataset (pd.DataFrame): The dataset containing 'engine_type' and 'fuel' columns.

    Returns:
        pd.DataFrame: Updated dataset with modified 'fuel' column.
    """
    # Filter the rows matching the condition
    condition = (dataset['engine_type'] == 'hybrid') & (dataset['fuel'] == 'Petrol')

    # Update the fuel column for rows that meet the condition
    dataset.loc[condition, 'fuel'] = 'Hybrid'

    return dataset

# Apply the function to your dataset
car_golf_dataset = update_fuel_type_to_hybrid(car_golf_dataset)

# Display the rows to verify
print(car_golf_dataset[car_golf_dataset['fuel'] == 'Hybrid'][['title', 'engine_type', 'fuel']])


                                                   title engine_type    fuel
2626   Volkswagen Golf VIII Lim. Style eHybrid DSG~LE...      hybrid  Hybrid
3703                Volkswagen Golf VIII 1.4 eHybrid GTE      hybrid  Hybrid
11323  Volkswagen Golf VIII Lim. GTE eHybrid LED NAVI...      hybrid  Hybrid
13315  Volkswagen Golf VIII 1.4 eHybrid GTE DSG + AHK...      hybrid  Hybrid
15410  Volkswagen Golf Style 1.4 eHybrid DSG LED-Plus...      hybrid  Hybrid
16419         Volkswagen Golf 1.4 GTE Plug-In-Hybrid DSG      hybrid  Hybrid
16547  Volkswagen Golf GTE VIII 1.4 eHybrid DSG NAVI,...      hybrid  Hybrid
22093  Volkswagen Golf VIII 1.4 eHybrid Style Style e...      hybrid  Hybrid
26710  Volkswagen Golf VIII 1.4 Style eHybrid AHK NAV...      hybrid  Hybrid
45920  Volkswagen Golf GTE 1,4 l E-Hybrid Rückfahrkam...      hybrid  Hybrid
51579  Volkswagen Golf 8 Style eHybrid IQ-LED/Navi/AC...      hybrid  Hybrid
56111  Volkswagen Golf VIII GTE 1.4 eHybrid DSG NAVI ...      hybrid  Hybrid

Note: I have updated the fuel type according to the engine type

### 2.4.1 Contradiction in title (DSG & hand)

In [90]:
# Convert the title column to lowercase
car_golf_dataset['title'] = car_golf_dataset['title'].str.lower()

# Filter rows where both 'dsg' and 'hand' are present in the title
dsg_hand_data = car_golf_dataset[
    car_golf_dataset['title'].str.contains('dsg', na=False) &
    car_golf_dataset['title'].str.contains('hand', na=False)
]

# Display the filtered rows
dsg_hand_data[['title', 'transmission']]

title  \
165    volkswagen golf vii sportsvan bluemotion *dsg*...   
508    volkswagen golf plus 1.2 tsi *dsg*1.hand*orig....   
509    volkswagen golf plus style/dsg/klima/1.hand/51...   
669    volkswagen golf 2.0tdi sportsvan dsg pano navi...   
836    volkswagen golf 2.0 tdi dsg klimatronic,leder,...   
...                                                  ...   
75137  volkswagen golf vii r bmt 4motion* abt 360ps* ...   
75666  volkswagen golf vii variant 1.5 tsi dsg iq.dri...   
75948  volkswagen golf 8 gtd 2.0 tdi dsg*navi*led*shz...   
76424  volkswagen golf vii variant rline dsgbmt/start...   
77674  volkswagen golf vii limousine 1.6 tdi scr dsg ...   

                 transmission  
165    Automatic transmission  
508    Automatic transmission  
509    Automatic transmission  
669    Automatic transmission  
836            Manual gearbox  
...                       ...  
75137               Automatic  
75666               Automatic  
75948               Automatic  
76424               Automatic  
77674               Automatic  

[224 rows x 2 columns]

In [91]:
def drop_rows_with_dsg_and_hand(dataset):
    """
    Drop rows where both 'dsg' and 'hand' appear in the title column.

    Parameters:
        dataset (pd.DataFrame): The dataset containing the 'title' column.

    Returns:
        pd.DataFrame: The updated dataset with the specified rows removed.
    """
    # Convert title column to lowercase for consistent matching
    dataset['title'] = dataset['title'].str.lower()

    # Define condition for rows containing both 'dsg' and 'hand'
    condition = dataset['title'].str.contains('dsg', na=False) & dataset['title'].str.contains('hand', na=False)

    # Drop rows that match the condition
    updated_dataset = dataset[~condition].reset_index(drop=True)

    return updated_dataset

# Apply the function to your dataset
car_golf_dataset = drop_rows_with_dsg_and_hand(car_golf_dataset)

# Display the dataset to confirm changes
print(car_golf_dataset.head())


   source_id                                              title    category  \
0  286354023  volkswagen golf -black weeks-fahrzeug, täglich...  Estate Car   
1  312826845  volkswagen golf var. vii 2.0 tdi dsg gtd sport...  Estate Car   
2  311592214  volkswagen golf vii sportsvan van/lounge 2.0 t...  Estate Car   
3  312569111  volkswagen golf  sportsvan 1.2 tsi lounge aac ...  Estate Car   
4  299066532  volkswagen golf 7 sportsvan allstar 1.6 tdi bm...  Estate Car   

         make model  power color  capacity            transmission    fuel  \
0  volkswagen  golf    123   NaN      1395          Manual gearbox  Petrol   
1  volkswagen  golf    181   NaN      1968  Automatic transmission  Diesel   
2  volkswagen  golf    148   NaN      1968  Automatic transmission  Diesel   
3  volkswagen  golf    109   NaN      1197          Manual gearbox  Petrol   
4  volkswagen  golf    109   NaN      1598          Manual gearbox  Diesel   

            construction_year  price_net  price_gross  \

### 2.4.2 title (hand) and transmission (Automatic) mismatch

"hand" appears in the title but the transmission is not manual

In [92]:
# Filter the rows where 'hand' appears in the title and transmission is not 'Manual gearbox'
hand_non_manual_data = car_golf_dataset[
    car_golf_dataset['title'].str.contains('hand', case=False, na=False) &
    (car_golf_dataset['transmission'] != 'Manual gearbox')
]

# Select relevant columns: title, engine_type, fuel, and transmission
hand_non_manual_data = hand_non_manual_data[['title', 'transmission']]

# Display the filtered data
hand_non_manual_data # Show first 10 rows of data where title contains 'hand' and transmission is not 'Manual gearbox'


title  \
460    volkswagen golf plus life 1,6l automatik 2.han...   
548    volkswagen golf plus autom/2.hand/scheckheft/k...   
798    volkswagen golf vi plus life 1.hand bi-xenon s...   
816    volkswagen golf vi plus trendline- klimaaut.-s...   
824    volkswagen golf vi plus life/1. hand/hu/au neu...   
...                                                  ...   
76649  volkswagen golf vii  gtd bmt+pano carbon steel...   
76999  volkswagen golf var. 1.5 highline, 1.hand,navi...   
77104  volkswagen golf viii variant life 2.0tdi |1.ha...   
77376  volkswagen golf vii comfortline  join aus 1. hand   
77484  volkswagen golf vii lim. trendline automatik  ...   

                 transmission  
460    Automatic transmission  
548    Automatic transmission  
798    Automatic transmission  
816    Automatic transmission  
824    Automatic transmission  
...                       ...  
76649               Automatic  
76999               Automatic  
77104               Automatic  
77376               Automatic  
77484               Automatic  

[317 rows x 2 columns]

 Update transmission to 'Manual gearbox' for rows where 'hand' appears in the title.

In [93]:
def update_transmission_to_manual(dataset):
    """
    Update transmission to 'Manual gearbox' for rows where 'hand' appears in the title.

    Parameters:
        dataset (pd.DataFrame): The dataset containing 'title' and 'transmission' columns.

    Returns:
        pd.DataFrame: Updated dataset with modified 'transmission' column.
    """
    # Filter rows where 'hand' appears in the title
    condition = dataset['title'].str.contains('hand', case=False, na=False)

    # Update the transmission column for rows matching the condition
    dataset.loc[condition, 'transmission'] = 'Manual gearbox'

    return dataset

# Apply the function to your dataset
car_golf_dataset = update_transmission_to_manual(car_golf_dataset)

# Verify the updates
print(car_golf_dataset[car_golf_dataset['title'].str.contains('hand', case=False, na=False)][['title', 'transmission']])


                                                   title    transmission
167    volkswagen golf plus 1.6 euro 5 life nur 39.65...  Manual gearbox
349    volkswagen golf vii variant lounge bmt,navi,sh...  Manual gearbox
460    volkswagen golf plus life 1,6l automatik 2.han...  Manual gearbox
522    volkswagen golf plus 1.4 tsi match-navi-1.hand...  Manual gearbox
548    volkswagen golf plus autom/2.hand/scheckheft/k...  Manual gearbox
...                                                  ...             ...
77406  volkswagen golf vi match bluemotion/bmt*1.hand...  Manual gearbox
77411  volkswagen golf vi 6 lim. 1.4 tsi match comfor...  Manual gearbox
77448  volkswagen golf vii variant sound 2.hand euro ...  Manual gearbox
77470  volkswagen golf vii lim.1hand!wie-neu!8tkm!nav...  Manual gearbox
77484  volkswagen golf vii lim. trendline automatik  ...  Manual gearbox

[1612 rows x 2 columns]


In [94]:
print(car_golf_dataset['transmission'].value_counts())

transmission
Automatic                 40168
Manual gearbox            34370
Automatic transmission     2250
automatic                   481
Semi-automatic              204
Name: count, dtype: int64


### 2.4.3 title (DSG) and transmission mismatch (Manual)

In [95]:
# Filter rows where 'DSG' is present in the title and transmission is not 'Automatic'
dsg_non_manual_data = car_golf_dataset[
    car_golf_dataset['title'].str.contains('DSG', case=False, na=False) &
    (car_golf_dataset['transmission'] == 'Manual gearbox')
]

# Display the filtered rows
dsg_non_manual_data[['title', 'transmission']]

title    transmission
1191   volkswagen golf vii 1,2 tsi dsg allstar (pdcpl...  Manual gearbox
1255   volkswagen golf variant viii life 2.0 tdi dsg ...  Manual gearbox
2785   volkswagen golf variant 2.0l tdi dsg pdc led n...  Manual gearbox
3296   volkswagen golf viii 2.0 tsi dsg r 4motion nav...  Manual gearbox
4289   volkswagen golf variant r-line 2.0 tdi dsg *na...  Manual gearbox
...                                                  ...             ...
76072  volkswagen volkswagen - golf - 2.0 tsi dsg 5p....  Manual gearbox
76274          volkswagen golf 1.5 tsi evo act style dsg  Manual gearbox
76516  volkswagen golf 1.5 etsi style dsg led navi ah...  Manual gearbox
77286    volkswagen golf 1.4 tgi dsg 5p. business 4 free  Manual gearbox
77308  volkswagen volkswagen golf variant 1.6 tdi 115...  Manual gearbox

[132 rows x 2 columns]

In [96]:
def update_transmission_to_automatic(dataset):
    """
    Update the 'transmission' column to 'Automatic' where 'DSG' is present in the title
    and the transmission is 'Manual gearbox'.

    Parameters:
        dataset (pd.DataFrame): The dataset containing 'title' and 'transmission' columns.

    Returns:
        pd.DataFrame: The updated dataset with the specified rows modified.
    """
    # Define the condition for rows to update
    condition = dataset['title'].str.contains('DSG', case=False, na=False) & (dataset['transmission'] == 'Manual gearbox')

    # Update the 'transmission' column where the condition is met
    dataset.loc[condition, 'transmission'] = 'Automatic'

    return dataset

# Apply the function to update the dataset
car_golf_dataset = update_transmission_to_automatic(car_golf_dataset)

# Verify changes
print(car_golf_dataset[car_golf_dataset['title'].str.contains('DSG', case=False, na=False)][['title', 'transmission']])


                                                   title  \
1      volkswagen golf var. vii 2.0 tdi dsg gtd sport...   
5      volkswagen golf vii sportsvan comfortline 1.6t...   
6      volkswagen golf vii variant 2.0 tdi dsg+highli...   
13     volkswagen golf vii dsg highline sport led*nav...   
14     volkswagen golf var. vii r 2.0 tsi dsg 4mo. ac...   
...                                                  ...   
77509  volkswagen golfvii*gti*tcr*dsg*virtual*kamera*...   
77511  volkswagen golf viii *united* 1.5 etsi dsg *na...   
77512  volkswagen golf viii 2.0 tsi dsg style navi ah...   
77518  volkswagen golf viii variant 2.0 tdi dsg life ...   
77519  volkswagen golf viii variant 2.0 tdi dsg led, ...   

                 transmission  
1      Automatic transmission  
5      Automatic transmission  
6      Automatic transmission  
13     Automatic transmission  
14     Automatic transmission  
...                       ...  
77509               Automatic  
77511               Aut

# PLOT

In [97]:
# Load the dataset (from the previous provided steps, filtered out 'unknown')
# Assuming `car_golf_dataset` already exists and 'unknown' rows are excluded.
filtered_data = car_golf_dataset[car_golf_dataset['engine_type'] != 'unknown']

# Group by category and engine_type and calculate counts
category_engine_count = filtered_data.groupby(['category', 'engine_type']).size().reset_index(name='count')

# Calculate total counts for percentage calculation
total_counts = category_engine_count.groupby('category')['count'].sum().reset_index()
total_counts.rename(columns={'count': 'total_count'}, inplace=True)

# Merge total counts to the original DataFrame
df = category_engine_count.merge(total_counts, on='category')

# Calculate the percentage
df['percentage'] = (df['count'] / df['total_count']) * 100

# Create an interactive bar chart using Plotly
fig = px.bar(df,
             x='category',
             y='percentage',
             color='engine_type',
             text='percentage',
             title='Percentage of Engine Type by Vehicle Categories',
             labels={'percentage': 'Percentage (%)', 'category': 'Vehicle Category', 'engine_type': 'Engine Type'},
             hover_data={'percentage': True})

# Update text and hover information
fig.update_traces(texttemplate='%{text:.2f}%', textposition='outside')

# Show the plot
fig.show()


The data indicates that "tsi" engines are predominant in most vehicle categories, particularly in "Cabriolet / Roadster," "Estate Car," "Saloon," and "Small Car," while "hybrid" engines have low adoption rates across all categories. Estate Cars favor "tsi" and "tdi" engines for performance and efficiency, whereas Small Cars show a broader range of engine types, reflecting diverse consumer preferences.

In [106]:
# Subplots: 2 rows, 2 columns
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=[
        'Mileage vs. Category ',
        'Mileage vs. Engine Type ',
        'Price (Net) vs. Category ',
        'Price (Net) vs. Engine Type '
    ],
)

# Add Box Plot 1: Mileage vs. Category
fig.add_trace(
    go.Box(
        y=filtered_data['mileage'],
        x=filtered_data['category'],
        marker_color='blue',
        name='Mileage by Category',
        boxmean=True
    ),
    row=1, col=1
)

# Add Box Plot 2: Mileage vs. Engine Type
fig.add_trace(
    go.Box(
        y=filtered_data['mileage'],
        x=filtered_data['engine_type'],
        marker_color='green',
        name='Mileage by Engine Type',
        boxmean=True
    ),
    row=1, col=2
)

# Add Box Plot 3: Price (Net) vs. Category
fig.add_trace(
    go.Box(
        y=filtered_data['price_net'],
        x=filtered_data['category'],
        marker_color='red',
        name='Price by Category',
        boxmean=True
    ),
    row=2, col=1
)

# Add Box Plot 4: Price (Net) vs. Engine Type
fig.add_trace(
    go.Box(
        y=filtered_data['price_net'],
        x=filtered_data['engine_type'],
        marker_color='purple',
        name='Price by Engine Type',
        boxmean=True
    ),
    row=2, col=2
)

# Update layout
fig.update_layout(
    title_text='Box Plots for Mileage and Price (Outliers Removed)',
    height=800,  # Set plot height
    width=1000,  # Set plot width
    showlegend=False,  # Disable individual legends to avoid clutter
)

# Update axis titles
fig.update_xaxes(title_text="Car Type", row=1, col=1)
fig.update_xaxes(title_text="Engine Type", row=1, col=2)
fig.update_xaxes(title_text="Car Type", row=2, col=1)
fig.update_xaxes(title_text="Engine Type", row=2, col=2)

fig.update_yaxes(title_text="Mileage", row=1, col=1)
fig.update_yaxes(title_text="Mileage", row=1, col=2)
fig.update_yaxes(title_text="Price (Net)", row=2, col=1)
fig.update_yaxes(title_text="Price (Net)", row=2, col=2)

# Show figure
fig.show()




The data indicates that Cabriolet/Roadster vehicles, despite having a smaller sample size, exhibit higher average mileage and smaller price range compared to other categories, suggesting they are often used more efficiently or have longer lifespans.Price trends reveal that "gti" and "gtd" engines typically have higher net prices, reflecting their performance-oriented nature compared to other engine types.